<a href="https://colab.research.google.com/github/coltongerth/Mimic3-viz/blob/main/MIMIC3_Viz.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [3]:
!pip install --upgrade chart_studio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.4/64.4 kB 1.8 MB/s eta 0:00:00


In [4]:
from google.colab import files, data_table
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import scipy.optimize
import chart_studio
import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px

data_table.enable_dataframe_formatter()

In [2]:
#@title Provide Google Credentials to Colab Runtime (May Require Manually Copy/Pasting Authentication Code)
from google.colab import auth
auth.authenticate_user()
print('Authenticated')

Authenticated


In [5]:
project_id = 'ai-in-healthcare-449320' #@param{type:"string"}

# Package used for interfacing w/ BigQuery from Python
from google.cloud import bigquery

# Create BigQuery client
bq_client = bigquery.Client(project = project_id)

First Visualization: Basic Patient Insurance Ratios using Plotly's Pie-chart.

In [ ]:
query = """
SELECT
  subject_id,
  insurance,
FROM `physionet-data.mimiciii_clinical.patients`
JOIN `physionet-data.mimiciii_clinical.admissions` USING (subject_id)

"""

df = bq_client.query(query).to_dataframe()
df

subject_id   insurance
0           18333     Private
1            7730     Private
2           11670     Private
3            8060     Private
4            8060     Private
...           ...         ...
58971       70330  Government
58972       70339  Government
58973       77623  Government
58974       43837  Government
58975       43878  Government

[58976 rows x 2 columns]

In [ ]:
insurance_counts = df['insurance'].value_counts().reset_index()
insurance_counts.columns = ['insurance', 'Count']

fig = px.pie(insurance_counts, names='insurance', values='Count',
             title='Insurance Distribution in ICU Patients')
fig.show()

Second Visualization: Comparison of Drug Induced Mortalities by Gender using Plotly's Bar-chart.

In [ ]:
query = """
SELECT
  row_id,
  gender,
  drg_mortality
FROM `physionet-data.mimiciii_clinical.patients`
JOIN `physionet-data.mimiciii_clinical.drgcodes` USING (row_id)

"""

df = bq_client.query(query).to_dataframe()
df

row_id gender  drg_mortality
0       41451      M              0
1          49      F           <NA>
2       17808      F           <NA>
3       17328      F           <NA>
4        7313      F           <NA>
...       ...    ...            ...
46515   31750      M              4
46516   31763      M              4
46517   31769      M              4
46518   31832      M              4
46519   31840      M              4

[46520 rows x 3 columns]

In [ ]:
df['drg_mortality_na'] = df['drg_mortality'].isna()
gender_counts = df.groupby(['gender', 'drg_mortality_na']).size().reset_index(name='count')
gender_counts['drg_mortality_na'] = gender_counts['drg_mortality_na'].map({True: 'Non-Mortality', False: 'Mortality'})

fig = px.bar(
    gender_counts,
    x='gender',
    y='count',
    color='drg_mortality_na',
    color_discrete_map={'Mortality': 'red', 'Non-Mortality': 'blue'},
    barmode='group',
    title='Comparison of Drug Induced Mortalities by Gender',
    labels={'count': 'Patient Count', 'gender': 'Gender', 'drg_mortality_na': 'DRG Mortality'}
)

fig.show()

Third Visualization: ICU Length of Stay vs Age using Plotly's Scatter Plot.

In [ ]:
query = """
SELECT
  subject_id,
  los,
  DATE_DIFF(DATE(admittime), DATE(dob), YEAR) AS age
FROM `physionet-data.mimiciii_clinical.patients`
JOIN `physionet-data.mimiciii_clinical.icustays` USING (subject_id)
JOIN `physionet-data.mimiciii_clinical.admissions` USING (subject_id)
WHERE DATE_DIFF(DATE(admittime), DATE(dob), YEAR) BETWEEN 1 AND 100
"""

df = bq_client.query(query).to_dataframe()
df


subject_id      los  age
0            27595  10.9331   32
1            31263   4.7062   18
2            27617   2.4125   19
3            27617   2.4125   19
4            27394  10.4183   22
...            ...      ...  ...
103022       77227   9.2669   88
103023       94221   1.9663   88
103024       93062   2.8454   88
103025       90296   1.8373   88
103026       96137   0.8634   88

[103027 rows x 3 columns]

In [ ]:
df['los'] = pd.to_numeric(df['los'], errors='coerce')
df['age'] = pd.to_numeric(df['age'], errors='coerce')

fig = px.scatter(
    df,
    x='age',
    y='los',
    title="ICU Length of Stay vs Age",
    labels={'age': 'Age (Years)', 'los': 'Length of Stay (Days)'},
    opacity=0.6
)

fig.show()

Fourth Visualization: ICU Admission Breakdown by Type and Gender using Plotly's Sunburst-graph

In [ ]:
query = """
SELECT
  admission_type,
  gender,
  COUNT(*) AS count
FROM `physionet-data.mimiciii_clinical.admissions`
JOIN `physionet-data.mimiciii_clinical.patients` USING (subject_id)
GROUP BY admission_type, gender
"""

df = bq_client.query(query).to_dataframe()

df

admission_type gender  count
0      EMERGENCY      F  18634
1       ELECTIVE      F   3174
2         URGENT      F    600
3        NEWBORN      F   3618
4      EMERGENCY      M  23437
5       ELECTIVE      M   4532
6         URGENT      M    736
7        NEWBORN      M   4245

In [ ]:
import plotly.express as px

fig = px.sunburst(
    df,
    path=['admission_type', 'gender'],
    values='count',
    title="ICU Admission Breakdown by Type and Gender",
    color='admission_type',
)

fig.show()

Fifth Visualization: ICU Length of Stay by Admission Type using Plotly's Box-Graph


In [ ]:
query = """
SELECT
  admission_type,
  los
FROM `physionet-data.mimiciii_clinical.icustays`
JOIN `physionet-data.mimiciii_clinical.admissions` USING (subject_id)
WHERE los IS NOT NULL
"""

df = bq_client.query(query).to_dataframe()
df

admission_type     los
0           EMERGENCY  6.2559
1           EMERGENCY  6.2559
2           EMERGENCY  6.2559
3           EMERGENCY  2.3403
4              URGENT  3.5888
...               ...     ...
116409      EMERGENCY  0.8539
116410       ELECTIVE  0.8539
116411      EMERGENCY  1.1919
116412      EMERGENCY  1.1919
116413       ELECTIVE  0.9259

[116414 rows x 2 columns]

In [ ]:
fig = px.box(df, x='admission_type', y='los', title="ICU Length of Stay by Admission Type",
             labels={'los': 'Length of Stay (Days)', 'admission_type': 'Admission Type'})

fig.show()

In [6]:
query = """
SELECT p.subject_id,
       COUNT(pr.drug) as prescription_count,
       p.gender,
       p.dob
FROM `physionet-data.mimiciii_clinical.patients` p
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
  ON p.subject_id = pr.subject_id
GROUP BY p.subject_id, p.gender, p.dob
HAVING COUNT(pr.drug) > 5
ORDER BY prescription_count DESC
LIMIT 10;
"""

df = bq_client.query(query).to_dataframe()
df

subject_id  prescription_count gender        dob
0       29035                2378      F 2089-12-13
1       11318                2313      F 2052-02-14
2       13033                2283      M 2148-04-23
3         109                2095      F 2117-08-07
4       19213                1994      F 2168-10-06
5       25256                1927      M 2123-03-28
6       25225                1927      F 2147-08-13
7        7809                1845      F 2078-12-05
8       11861                1779      F 2105-05-05
9       48872                1739      M 2131-07-16

In [20]:
query = """
SELECT
    d.icd9_code,
    diag.long_title,
    COUNT(DISTINCT pr.subject_id) as patient_count,
    COUNT(pr.drug) as prescription_count
FROM `physionet-data.mimiciii_clinical.diagnoses_icd` d
JOIN `physionet-data.mimiciii_clinical.d_icd_diagnoses` diag
    ON d.icd9_code = diag.icd9_code
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
    ON d.hadm_id = pr.hadm_id
GROUP BY d.icd9_code, diag.long_title
ORDER BY prescription_count DESC
LIMIT 15;
"""

df = bq_client.query(query).to_dataframe()
df

icd9_code                                         long_title  \
0       4019                 Unspecified essential hypertension   
1      42731                                Atrial fibrillation   
2       4280              Congestive heart failure, unspecified   
3      41401  Coronary atherosclerosis of native coronary ar...   
4       5849                  Acute kidney failure, unspecified   
5      51881                          Acute respiratory failure   
6      25000  Diabetes mellitus without mention of complicat...   
7       2724               Other and unspecified hyperlipidemia   
8       5990        Urinary tract infection, site not specified   
9      99592                                      Severe sepsis   
10     53081                                  Esophageal reflux   
11       486                    Pneumonia, organism unspecified   
12      2859                                Anemia, unspecified   
13      2762                                           Acidosis   
14      0389                             Unspecified septicemia   

    patient_count  prescription_count  
0           16311             1657266  
1            9590             1269253  
2            9100             1234851  
3            9690             1019345  
4            7385              931470  
5            6299              927047  
6            6843              778319  
7            7370              746667  
8            5432              689830  
9            3558              568862  
10           5041              510380  
11           4129              502008  
12           4751              501271  
13           3958              472784  
14           3262              446892

In [46]:
query = """
SELECT drug_category,
       AVG(los) as avg_length_of_stay,
       COUNT(DISTINCT subject_id) as patient_count
FROM (
  SELECT pr.subject_id,
         pr.drug,
         pr.drug_type as drug_category,
         DATETIME_DIFF(a.dischtime, a.admittime, DAY) as los
  FROM `physionet-data.mimiciii_clinical.prescriptions` pr
  JOIN `physionet-data.mimiciii_clinical.admissions` a
    ON pr.hadm_id = a.hadm_id
)
GROUP BY drug_category
HAVING patient_count > 50
ORDER BY avg_length_of_stay DESC;
"""

df = bq_client.query(query).to_dataframe()
df

drug_category  avg_length_of_stay  patient_count
0      ADDITIVE           30.734098           4200
1          BASE           19.585512          38594
2          MAIN           17.389872          39359

In [35]:
query = """
SELECT
  CASE
    WHEN age < 18 THEN 'Pediatric'
    WHEN age < 30 THEN 'Young Adult'
    WHEN age < 50 THEN 'Adult'
    WHEN age < 70 THEN 'Middle Aged'
    ELSE 'Elderly'
  END as age_group,
  COUNT(DISTINCT pr.subject_id) as patient_count,
  pr.drug_name_generic
FROM (
  SELECT
    subject_id,
    DATETIME_DIFF(DATETIME(dod), DATETIME(dob), YEAR) as age
  FROM `physionet-data.mimiciii_clinical.patients`
) p
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
  ON p.subject_id = pr.subject_id
WHERE pr.drug_name_generic IS NOT NULL
GROUP BY age_group, pr.drug_name_generic
ORDER BY patient_count DESC;
"""

df = bq_client.query(query).to_dataframe()
df

age_group  patient_count                     drug_name_generic
0         Elderly          25451           Sodium Chloride 0.9%  Flush
1         Elderly          24429                         Acetaminophen
2         Elderly          20935                       Docusate Sodium
3         Elderly          20782                        Heparin Sodium
4         Elderly          18779                    Potassium Chloride
...           ...            ...                                   ...
6138      Elderly              1   Mesalamine Desensitization Dose # 7
6139      Elderly              1   Mesalamine Desensitization Dose # 8
6140  Middle Aged              1  Phenytoin Sodium **Brand Name ONLY**
6141  Young Adult              1                      Digoxin (Elixir)
6142  Middle Aged              1             Humalog Mix 75-25 KwikPen

[6143 rows x 3 columns]

In [33]:
query = """
SELECT
  p.gender,
  pr.drug_name_generic,
  COUNT(DISTINCT p.subject_id) as patient_count,
FROM `physionet-data.mimiciii_clinical.patients` p
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
  ON p.subject_id = pr.subject_id
WHERE pr.drug_name_generic IS NOT NULL
GROUP BY p.gender, pr.drug_name_generic
HAVING patient_count > 100
ORDER BY p.gender, patient_count DESC;

"""

df = bq_client.query(query).to_dataframe()
df

gender                  drug_name_generic  patient_count
0        F        Sodium Chloride 0.9%  Flush          12751
1        F                      Acetaminophen          12355
2        F                     Heparin Sodium          11032
3        F                    Docusate Sodium          10344
4        F                 Potassium Chloride           9560
..     ...                                ...            ...
915      M                          Sirolimus            103
916      M                   Pioglitazone HCl            102
917      M          Megestrol Oral Suspension            101
918      M                Nitroglycerin Patch            101
919      M  Lidocaine 1%/Epinephrine 1:100000            101

[920 rows x 3 columns]

In [37]:
query = """
WITH readmissions AS (
  SELECT
    subject_id,
    COUNT(hadm_id) as admission_count
  FROM `physionet-data.mimiciii_clinical.admissions`
  GROUP BY subject_id
  HAVING COUNT(hadm_id) > 1
)
SELECT
  r.admission_count,
  COUNT(DISTINCT pr.drug) as unique_drugs,
FROM readmissions r
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
  ON r.subject_id = pr.subject_id
GROUP BY r.admission_count
ORDER BY r.admission_count DESC;
"""

df = bq_client.query(query).to_dataframe()
df

admission_count  unique_drugs
0                42           164
1                34           251
2                31           108
3                24           155
4                23           182
5                22           172
6                21           156
7                20           117
8                19           194
9                17           264
10               16           211
11               15           141
12               14           324
13               13           352
14               12           451
15               11           567
16               10           490
17                9           690
18                8           742
19                7           754
20                6          1030
21                5          1193
22                4          1468
23                3          1846
24                2          2560

In [42]:
query = """
SELECT
  pr.drug_name_generic,
  COUNT(DISTINCT CASE WHEN p.dod IS NOT NULL THEN p.subject_id END) as deceased_count,
  COUNT(DISTINCT p.subject_id) as total_patients,
  ROUND(COUNT(DISTINCT CASE WHEN p.dod IS NOT NULL THEN p.subject_id END) /
        COUNT(DISTINCT p.subject_id) * 100, 2) as mortality_rate
FROM `physionet-data.mimiciii_clinical.patients` p
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
  ON p.subject_id = pr.subject_id
GROUP BY pr.drug_name_generic
HAVING total_patients > 100
ORDER BY mortality_rate DESC;
"""

df = bq_client.query(query).to_dataframe()
df

drug_name_generic  deceased_count  \
0    Morphine Sulfate (Concentrated Oral Soln)             433   
1                            Scopolamine Patch            1488   
2                                  Hyoscyamine             332   
3                                 Voriconazole             185   
4                                   Salmeterol              82   
..                                         ...             ...   
618              NEO*PO*Ferrous Sulfate Elixer               0   
619            NEO*SC*Polio Vaccine (Inactive)               0   
620                        Multivitamin Liquid               0   
621                     Pediatric Vitamins ADC               0   
622               Vi-Daylin Multivitamin Drops               0   

     total_patients  mortality_rate  
0               495           87.47  
1              1706           87.22  
2               395           84.05  
3               224           82.59  
4               103           79.61  
..              ...             ...  
618             131            0.00  
619             113            0.00  
620             304            0.00  
621             206            0.00  
622             158            0.00  

[623 rows x 4 columns]

In [41]:
query = """
SELECT
  EXTRACT(MONTH FROM startdate) as month,
  drug_type,
  COUNT(*) as prescription_count
FROM `physionet-data.mimiciii_clinical.prescriptions`
GROUP BY month, drug_type
ORDER BY month, prescription_count DESC;
"""

df = bq_client.query(query).to_dataframe()
df

month drug_type  prescription_count
0    <NA>      MAIN                3181
1    <NA>      BASE                   1
2       1      MAIN              279753
3       1      BASE               80503
4       1  ADDITIVE                1279
5       2      MAIN              257506
6       2      BASE               73328
7       2  ADDITIVE                1110
8       3      MAIN              275692
9       3      BASE               78487
10      3  ADDITIVE                1337
11      4      MAIN              265978
12      4      BASE               76524
13      4  ADDITIVE                1153
14      5      MAIN              271644
15      5      BASE               77646
16      5  ADDITIVE                1177
17      6      MAIN              258364
18      6      BASE               74463
19      6  ADDITIVE                1015
20      7      MAIN              266656
21      7      BASE               77592
22      7  ADDITIVE                1258
23      8      MAIN              278856
24      8      BASE               82430
25      8  ADDITIVE                1334
26      9      MAIN              259829
27      9      BASE               74519
28      9  ADDITIVE                1163
29     10      MAIN              264975
30     10      BASE               74868
31     10  ADDITIVE                1252
32     11      MAIN              261511
33     11      BASE               75859
34     11  ADDITIVE                1115
35     12      MAIN              272937
36     12      BASE               78869
37     12  ADDITIVE                1286

In [18]:
query = """
SELECT
  icu.subject_id,
  COUNT(DISTINCT pr.drug) as unique_medications,
  AVG(DATETIME_DIFF(icu.outtime, icu.intime, HOUR)) as icu_hours
FROM `physionet-data.mimiciii_clinical.icustays` icu
JOIN `physionet-data.mimiciii_clinical.prescriptions` pr
  ON icu.subject_id = pr.subject_id
GROUP BY icu.subject_id
HAVING icu_hours > 24
ORDER BY unique_medications DESC
LIMIT 20;
"""

df = bq_client.query(query).to_dataframe()
df

subject_id  unique_medications    icu_hours
0        29035                 220   124.647059
1        25225                 214   128.200000
2        25256                 211   290.866667
3        21280                 199   552.222222
4        27172                 197   258.800000
5        13373                 196    86.100000
6        11318                 194    95.090909
7        55973                 190    95.733333
8        18982                 189   185.363636
9         7666                 183   213.111111
10       21202                 183   127.700000
11        5774                 182   144.800000
12       55337                 182   208.333333
13       19213                 182    61.440000
14       48872                 181   298.142857
15         109                 179    58.973684
16       22933                 177    97.533333
17       12613                 175  2149.000000
18       26274                 175   105.777778
19       28972                 173   376.500000

In [19]:
query = """
WITH drug_pairs AS (
  SELECT
    a.subject_id,
    a.drug as drug1,
    b.drug as drug2
  FROM `physionet-data.mimiciii_clinical.prescriptions` a
  JOIN `physionet-data.mimiciii_clinical.prescriptions` b
    ON a.subject_id = b.subject_id
    AND a.drug < b.drug
    AND a.startdate BETWEEN b.startdate
    AND DATE_ADD(b.startdate, INTERVAL 7 DAY)
)
SELECT
  drug1,
  drug2,
  COUNT(DISTINCT subject_id) as patient_count
FROM drug_pairs
GROUP BY drug1, drug2
HAVING patient_count > 50
ORDER BY patient_count DESC;
"""

df = bq_client.query(query).to_dataframe()
df

drug1                             drug2  \
0            Magnesium Sulfate                Potassium Chloride   
1                Acetaminophen       Sodium Chloride 0.9%  Flush   
2           Potassium Chloride       Sodium Chloride 0.9%  Flush   
3            Magnesium Sulfate       Sodium Chloride 0.9%  Flush   
4                      Insulin       Sodium Chloride 0.9%  Flush   
...                        ...                               ...   
48453                Albuterol  Amino Acids 4.25% W/ Dextrose 5%   
48454  Chlorhexidine Gluconate                       Haloperidol   
48455         Acetaminophen IV              Ampicillin-Sulbactam   
48456     Escitalopram Oxalate       Iso-Osmotic Sodium Chloride   
48457          Docusate Sodium                         RiTONAvir   

       patient_count  
0              22583  
1              22215  
2              22015  
3              19702  
4              19499  
...              ...  
48453             51  
48454             51  
48455             51  
48456             51  
48457             51  

[48458 rows x 3 columns]